In [ ]:
import json
import re
import pandas as pd
import scrapy
import shutil
import os
import numpy as np

In [ ]:
!scrapy startproject tripadvisorVNAttraction

In [ ]:
%cd tripadvisorVNAttraction/tripadvisorVNAttraction

In [ ]:
url_spider_text='''\
import scrapy
class MySpider(scrapy.Spider):
    name = 'VNAttraction'
    #custom_settings = { 'CONCURRENT_REQUESTS': '1' }
    def start_requests(self):
        for page in range (round(11544/30)+1):
            yield scrapy.Request(f'https://www.tripadvisor.com/Attractions-g293921-Activities-oa{page*30}-Vietnam.html',self.parse)
        #yield scrapy.Request(f'https://www.tripadvisor.com/Attractions-g293921-Activities-oa{60}-Vietnam.html',self.parse)
    def parse(self, response):
        attraction_url= response.xpath("//section//a/@href").getall()
        attraction_url=[i for i in attraction_url if 'Attraction_Review' in i and '#REVIEWS' not in i]
        attraction_url = dict.fromkeys(attraction_url).keys()
        rank=response.xpath("//section//a//span[@name='title']//span/text()").getall()
        rank= [int(i[:-1]) for i in rank]
        name= response.xpath("//section//a//span[@name='title']/div/text()[2]").getall()
        url_rank={'rank':rank,'name':name,'attraction_url':attraction_url}
        url_rank=[dict(zip(url_rank,t)) for t in zip(*url_rank.values())]
        for i in url_rank : yield i

'''

if os.path.exists("./spiders/urls.py"):
    os.remove("./spiders/urls.py")
f=open("./spiders/urls.py",'w+')
f.write(url_spider_text)
f.close()

In [ ]:
url_spider_text='''\
import scrapy
import re
import json
class MySpider(scrapy.Spider):
    name = 'AttractionReviews'
    domain_en='https://www.tripadvisor.com'
    domain_vi='https://www.tripadvisor.com.vn'
    url='/Attraction_Review-g293924-d25191362-Reviews-K_Hair_Studio-Hanoi.html'
    #custom_settings = { 'ROBOTSTXT_OBEY': False }
    def start_requests(self):
        with open('./dataset/urls.json') as f:
            url=json.load(f)
        for i in url :
            yield scrapy.Request(f'{self.domain_en}{i["attraction_url"]}',self.check_en)
            yield scrapy.Request(f'{self.domain_vi}{i["attraction_url"]}',self.check_vi)
    def check_en(self, response):
        numpage= response.xpath("//section[@id='REVIEWS']//div[@class='Ci']/text()[6]").get()
        if numpage : 
            numpage=int(numpage.replace(',',''))
            for i in self.parse_en(response) : yield i
            for i in range(1,round(numpage/10)+1):
                yield scrapy.Request(response.url.replace('-Reviews',f'-Reviews-or{i*10}'),self.parse_en)
        else :
            for i in self.parse_en(response) : yield i
    def parse_en(self, response):
        print(response.url)
        if response.xpath("//section[@id='REVIEWS']//div[@class='C' and @data-ft='true']//button[contains(@aria-label,'English')]").getall() :
            
            reviews= response.xpath("//section[@id='REVIEWS']//div[@class='C' and @data-ft='true']/div[@data-automation='reviewCard']").getall()
            reviews=[scrapy.Selector(text=i) for i in reviews]
            if reviews :
                names=[]
                links=[]
                for i in reviews:
                    try :
                        links.append(self.domain_en+i.xpath("//a[@target='_self']/@href").get())
                        names.append(i.xpath("//a[@target='_self']/text()").get())
                    except:
                        names.append(i.xpath("//span/text()").get())
                        links.append('')
                upvotes=[i.xpath("//div[@class='f']//span/span/text()").get() for i in reviews]

                describes=[i.xpath("//a[@target='_self']/../../div/div/span/text()").getall() for i in reviews]
                contributions=[i[-1].replace('contributions','') if len(i)>0 else 0 for i in describes]
                homeplaces=[i[-2] if len(i)>1 else '' for i in describes]

                rates=[]
                for i in reviews:
                    try :
                        rates.append(i.xpath("//svg/@aria-label").get().split(' ')[0])
                    except:
                        rates.append('3.0')
                
                titles=[i.xpath("//a[@target='_blank']/span/text()").get() for i in reviews]

                triptimes=[]
                tripwiths=[]
                contents=[]
                for i in reviews:
                    try :
                        tripinfos=i.xpath("//div[4]/text()").get().split('•')
                        triptimes.append(tripinfos[0] if len(tripinfos)>0 else '')
                        tripwiths.append(tripinfos[1] if len(tripinfos)>1 else '')
                        contents.append(' '.join(i.xpath("//div[5]/div[1]/div/span/text()").getall()).strip())
                    except:
                        triptimes.append('')
                        tripwiths.append('')
                        try:
                            contents.append(' '.join(i.xpath("//div[4]/div[1]/div/span/text()").getall()).strip())
                        except:
                            contents.append('')
                
                writtentimes=[i.xpath("//div[contains(text(),'not of Tripadvisor LLC')]/../div[1]/text()").get() for i in reviews]
                writtentimes=[i.split('Written ')[1] if (i) else '' for i in writtentimes]
                
                commentdict={
                    'weburl':[re.sub("Reviews\-or[0-9]{,}",'Reviews', response.url)]*len(names),
                    'name':names,
                    'link':links,
                    'upvote':upvotes,
                    'contributions':contributions,
                    'homeplace':homeplaces,
                    'rate':rates,
                    'title':titles,
                    'triptime':triptimes,
                    'tripwith':tripwiths,
                    'content':contents,
                    'writtentime':writtentimes,
                    'language':['en']*len(names),
                }
                commentdict=[dict(zip(commentdict,t)) for t in zip(*commentdict.values())]
                for i in commentdict : yield i
    def check_vi(self, response):
        numpage= response.xpath("//section[@id='REVIEWS']//div[@class='Ci']/text()[6]").get()
        if numpage : 
            numpage=int(numpage.replace(',',''))
            for i in self.parse_vi(response) : yield i
            for i in range(1,round(numpage/10)+1):
                yield scrapy.Request(response.url.replace('-Reviews',f'-Reviews-or{i*10}'),self.parse_vi)
        else :
            for i in self.parse_vi(response) : yield i
    def parse_vi(self, response):
        print(response.url)
        if response.xpath("//section[@id='REVIEWS']//div[@class='C' and @data-ft='true']//button[contains(@aria-label,'Tiếng Việt')]").getall() :
            reviews= response.xpath("//section[@id='REVIEWS']//div[@class='C' and @data-ft='true']/div[@data-automation='reviewCard']").getall()
            reviews=[scrapy.Selector(text=i) for i in reviews]

            if reviews :
                names=[]
                links=[]
                for i in reviews:
                    try :
                        links.append(self.domain_en+i.xpath("//a[@target='_self']/@href").get())
                        names.append(i.xpath("//a[@target='_self']/text()").get())
                    except:
                        names.append(i.xpath("//span/text()").get())
                        links.append('')
                upvotes=[i.xpath("//div[@class='f']//span/span/text()").get() for i in reviews]

                describes=[i.xpath("//a[@target='_self']/../../div/div/span/text()").getall() for i in reviews]
                contributions=[i[-1].replace('đóng góp','') if len(i)>0 else 0 for i in describes]
                homeplaces=[i[-2] if len(i)>1 else '' for i in describes]

                titles=[i.xpath("//a[@target='_blank']/span/text()").get() for i in reviews]

                rates=[]
                for i in reviews:
                    try :
                        rates.append(i.xpath("//svg/@aria-label").get().split(' ')[0])
                    except:
                        rates.append('3.0')
                
                titles=[i.xpath("//a[@target='_blank']/span/text()").get() for i in reviews]

                triptimes=[]
                tripwiths=[]
                contents=[]
                for i in reviews:
                    try :
                        tripinfos=i.xpath("//div[4]/text()").get().split('•')
                        triptimes.append(tripinfos[0] if len(tripinfos)>0 else '')
                        tripwiths.append(tripinfos[1] if len(tripinfos)>1 else '')
                        contents.append(' '.join(i.xpath("//div[5]/div[1]/div/span/text()").getall()).strip())
                    except:
                        triptimes.append('')
                        tripwiths.append('')
                        try:
                            contents.append(' '.join(i.xpath("//div[4]/div[1]/div/span/text()").getall()).strip())
                        except:
                            contents.append('')

                writtentimes=[i.xpath("//div[contains(text(),'không phải của Tripadvisor LLC')]/../div[1]/text()").get() for i in reviews]
                writtentimes=[i.split('Đã viết vào ')[1] if (i) else '' for i in writtentimes]
                
                commentdict={
                    'weburl':[re.sub("Reviews\-or[0-9]{,}",'Reviews', response.url).replace(self.domain_vi,self.domain_en)]*len(names),
                    'name':names,
                    'link':links,
                    'upvote':upvotes,
                    'contributions':contributions,
                    'homeplace':homeplaces,
                    'rate':rates,
                    'title':titles,
                    'triptime':triptimes,
                    'tripwith':tripwiths,
                    'content':contents,
                    'writtentime':writtentimes,
                    'language':['vi']*len(names),
                }
                commentdict=[dict(zip(commentdict,t)) for t in zip(*commentdict.values())]
                for i in commentdict : yield i


'''

if os.path.exists("./spiders/comments.py"):
    os.remove("./spiders/comments.py")
f=open("./spiders/comments.py",'w+')
f.write(url_spider_text)
f.close()

In [ ]:
if os.path.exists("./dataset/urls.json"):
    os.remove("./dataset/urls.json")
!scrapy crawl VNAttraction -o dataset/urls.json

In [ ]:
if os.path.exists("./dataset/cmts.json"):
    os.remove("./dataset/cmts.json")
!scrapy crawl AttractionReviews -o dataset/cmts.json

In [18]:
with open("./dataset/countcmts.json") as f:
    f.close()

!scrapy crawl countcmts -o dataset/countcmts.json

2022-12-16 12:30:26 [scrapy.utils.log] INFO: Scrapy 2.7.1 started (bot: tripadvisorVNAttraction)
2022-12-16 12:30:26 [scrapy.utils.log] INFO: Versions: lxml 4.9.1.0, libxml2 2.9.12, cssselect 1.2.0, parsel 1.7.0, w3lib 2.1.0, Twisted 22.10.0, Python 3.7.8 (tags/v3.7.8:4b47a5b6ba, Jun 28 2020, 08:53:46) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 22.1.0 (OpenSSL 3.0.7 1 Nov 2022), cryptography 38.0.4, Platform Windows-10-10.0.19041-SP0
2022-12-16 12:30:26 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'tripadvisorVNAttraction',
 'NEWSPIDER_MODULE': 'tripadvisorVNAttraction.spiders',
 'REQUEST_FINGERPRINTER_IMPLEMENTATION': '2.7',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['tripadvisorVNAttraction.spiders'],
 'TWISTED_REACTOR': 'twisted.internet.asyncioreactor.AsyncioSelectorReactor'}
2022-12-16 12:30:26 [asyncio] DEBUG: Using selector: SelectSelector
2022-12-16 12:30:26 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.asyncioreactor.AsyncioSelectorReactor
2022-12-16 12:3

In [1]:
import json 
import pandas as pd
with open('./cmts.json') as f :
    count=json.load(f)
df=pd.DataFrame(count)

In [8]:
df.to_csv('cmts.csv',encoding='utf-8-sig')